In [1]:
import requests
import pandas as pd
import numpy as np

http_proxy  = "http://proxy-web.micron.com:80"
https_proxy = "http://proxy-web.micron.com:80"
proxyDict = { 
    "http":http_proxy, 
    "https":https_proxy              
}

pd.set_option('display.max_rows', None) #show every row for pandas
pd.set_option('display.max_columns', None) #show every column for pandas

In [2]:
# sii:上市, otc:上櫃
# TWSE之數據是至該季的累計數據而非單季數據, EX: Q3=> TWSE: Q1~Q3, 財報狗:Q3
def financial_statement(year, season, stocktype, type='綜合損益彙總表'):
    if year >= 1000:
        year -= 1911
        
    if type == '綜合損益彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb04'
    elif type == '資產負債彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb05'
    elif type == '營益分析彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb06'
    else:
        print('type does not match')
    
    r = requests.post(url, {
        'encodeURIComponent':1,
        'step':1,
        'firstin':1,
        'off':1,
        'TYPEK':stocktype,
        'year':str(year),
        'season':str(season),
    }, stream=True, verify=False, proxies=proxyDict)
    
    r.encoding = 'utf8'
    dfs = pd.read_html(r.text)
    
    
    for i, df in enumerate(dfs):
        df.columns = df.iloc[0]
        dfs[i] = df.iloc[1:]
        
    df = pd.concat(dfs).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df['公司代號'] != '公司代號']
    df = df[~df['公司代號'].isnull()]
    
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_suffix.html
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_prefix.html
    suffix_format = "_{0}Q{1}".format(year, season)
    
    #return df.add_suffix(suffix_format)
    return df

In [3]:
def generate_df_for_stocktype(year, season, howmany_year_data, stocktype, title_name, with_col_name, sheettype):
    df = financial_statement(year, season, stocktype, type=sheettype)[['公司代號','公司名稱',with_col_name]]
    df.rename(columns = {df.columns[2]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

    for i in range(howmany_year_data*4):
        # calculate previous quarter data 107Q1 => we want the previous data is 106Q4 AND then 106Q3, 106Q2, 106Q1, 105Q4
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        #https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.merge.html
        dfanother = financial_statement(year, season, stocktype, type=sheettype)[['公司代號',with_col_name]]    
        print(dfanother.columns[1])

        dfanother.rename(columns = {dfanother.columns[1]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

        df = df.merge(dfanother, on='公司代號', how='inner')
        print("year:", year)
        #print("year: {0}".format(year))
        print("season:", season)
        #print("season: {0}".format(season))

    return df

In [4]:
df_gross_profit_sii = generate_df_for_stocktype(107, 1, 3, 'sii', 'GrossProfitMargin', '毛利率(%)(營業毛利)/(營業收入)', '營益分析彙總表')

df_gross_profit_sii

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



毛利率(%)(營業毛利)/(營業收入)
year: 106
season: 4
毛利率(%)(營業毛利)/(營業收入)
year: 106
season: 3
毛利率(%)(營業毛利)/(營業收入)
year: 106
season: 2
毛利率(%)(營業毛利)/(營業收入)
year: 106
season: 1
毛利率(%)(營業毛利)/(營業收入)
year: 105
season: 4
毛利率(%)(營業毛利)/(營業收入)
year: 105
season: 3
毛利率(%)(營業毛利)/(營業收入)
year: 105
season: 2
毛利率(%)(營業毛利)/(營業收入)
year: 105
season: 1
毛利率(%)(營業毛利)/(營業收入)
year: 104
season: 4
毛利率(%)(營業毛利)/(營業收入)
year: 104
season: 3
毛利率(%)(營業毛利)/(營業收入)
year: 104
season: 2
毛利率(%)(營業毛利)/(營業收入)
year: 104
season: 1


公司代號     公司名稱 GrossProfitMargin(%)_107Q1 GrossProfitMargin(%)_106Q4  \
0    1101       台泥                      23.95                      19.24   
1    1102       亞泥                      20.09                      15.67   
2    1103       嘉泥                      11.63                      13.47   
3    1104     環球水泥                      11.88                      12.21   
4    1108     幸福水泥                       2.47                       3.74   
5    1109     信大水泥                      22.71                      23.36   
6    1110       東泥                       8.35                      -2.52   
7    1201     味全公司                      28.20                      31.29   
8    1203     味王公司                      33.75                      32.61   
9    1210     大成長城                      14.90                      13.48   
10   1213       大飲                      10.74                      10.54   
11   1215     卜蜂企業                      14.78                      16.75   
12   1216       統一                      33.97                      33.20   
13   1217      愛之味                      31.66                      31.46   
14   1218     泰山企業                      16.56                      17.34   
15   1219     福壽實業                       9.32                       8.28   
16   1220       台榮                      11.49                      11.62   
17   1225      福懋油                       8.99                       9.63   
18   1227       佳格                      30.87                      27.95   
19   1229     聯華實業                      16.62                      21.16   
20   1231     聯華食品                      22.76                      20.56   
21   1232      大統益                      10.43                       9.98   
22   1233       天仁                      58.11                      56.91   
23   1234       黑松                      20.48                      25.69   
24   1235       興泰                     -10.29                       6.24   
25   1236     宏亞食品                      28.20                      26.76   
26   1256  鮮活果汁-KY                      31.63                      29.92   
27   1262    綠悅-KY                       7.73                      22.15   
28   1301       台塑                      17.26                      16.19   
29   1303     南亞塑膠                      16.75                      16.32   
30   1304       台聚                      12.58                      12.26   
31   1305       華夏                      23.41                      18.89   
32   1307     三芳化工                      23.21                      29.46   
33   1308       亞聚                       5.87                      10.88   
34   1309     台達化工                       7.75                       7.23   
35   1310       台苯                      13.64                      11.45   
36   1312     國喬石化                      17.61                      16.25   
37   1313       聯成                       7.51                       7.63   
38   1314      中石化                      13.25                      16.11   
39   1315     達新工業                      14.33                      16.71   
40   1316       上曜                      32.49                      29.35   
41   1319       東陽                      23.43                      24.23   
42   1321       大洋                       6.76                       5.64   
43   1323       永裕                      23.66                      23.64   
44   1324     地球工業                      14.99                      15.22   
45   1325       恒大                      11.55                      13.66   
46   1326       台化                      15.92                      14.84   
47   1337    再生-KY                     -12.37                      15.07   
48   1338    廣華-KY                      25.25                      26.41   
49   1339       昭輝                      30.02                      30.96   
50   1340    勝悅-KY                      28.59                      34.39   
51   1402      遠東新                      20.92        

In [5]:
df_gross_profit_otc = generate_df_for_stocktype(107, 1, 3, 'otc', 'GrossProfitMargin', '毛利率(%)(營業毛利)/(營業收入)', '營益分析彙總表')

df_gross_profit_otc

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



毛利率(%)(營業毛利)/(營業收入)
year: 106
season: 4
毛利率(%)(營業毛利)/(營業收入)
year: 106
season: 3
毛利率(%)(營業毛利)/(營業收入)
year: 106
season: 2
毛利率(%)(營業毛利)/(營業收入)
year: 106
season: 1
毛利率(%)(營業毛利)/(營業收入)
year: 105
season: 4
毛利率(%)(營業毛利)/(營業收入)
year: 105
season: 3
毛利率(%)(營業毛利)/(營業收入)
year: 105
season: 2
毛利率(%)(營業毛利)/(營業收入)
year: 105
season: 1
毛利率(%)(營業毛利)/(營業收入)
year: 104
season: 4
毛利率(%)(營業毛利)/(營業收入)
year: 104
season: 3
毛利率(%)(營業毛利)/(營業收入)
year: 104
season: 2
毛利率(%)(營業毛利)/(營業收入)
year: 104
season: 1


公司代號    公司名稱 GrossProfitMargin(%)_107Q1 GrossProfitMargin(%)_106Q4  \
0    1258   其祥-KY                      16.52                      17.67   
1    1259      安心                      24.35                      25.95   
2    1264      德麥                      37.15                      37.70   
3    1333     恩得利                      10.33                      12.16   
4    1336      台翰                      14.99                      16.93   
5    1565    精華光學                      36.64                      39.65   
6    1566      捷邦                      12.30                      14.36   
7    1569      濱川                      18.04                      22.56   
8    1570    力肯實業                      22.84                      23.49   
9    1580    新麥企業                      40.45                      41.13   
10   1584    精剛精密                       2.92                       3.00   
11   1586    和勤精機                      16.47                      20.51   
12   1591   駿吉-KY                       7.48                      16.91   
13   1593      祺驊                      26.17                      31.32   
14   1595    川寶科技                      27.75                      31.57   
15   1597      直得                      47.83                      41.86   
16   1599     宏佳騰                      17.56                      24.38   
17   1742      台蠟                       4.86                      10.72   
18   1752      南光                      34.89                      34.34   
19   1777      生泰                      32.91                      28.75   
20   1781    合世生醫                       5.30                       9.93   
21   1784    訊聯生技                      58.62                      52.51   
22   1785     光洋科                       9.27                      10.47   
23   1787     福盈科                      33.22                      32.26   
24   1788    杏昌生技                      21.84                      22.60   
25   1795    美時製藥                      45.86                      47.94   
26   1799      易威                       9.87                       9.73   
27   1813     寶利徠                      14.00                      20.66   
28   1815    富喬工業                      27.82                      27.22   
29   2035    唐榮公司                      -1.72                       2.86   
30   2061      風青                       4.36                       5.93   
31   2063      世鎧                      32.17                      29.40   
32   2064      晉椿                       9.43                       9.30   
33   2066      世德                      23.34                      28.71   
34   2067      嘉鋼                      15.84                      15.45   
35   2221    大甲永和                      24.84                      24.55   
36   2230      泰茂                      12.48                      18.84   
37   2233      宇隆                      39.73                      40.06   
38   2235      謚源                      24.40                      29.28   
39   2596    綠意開發                      47.14                      39.76   
40   2640     大車隊                      46.91                      46.43   
41   2641    正德海運                      23.91                      12.98   
42   2718      晶悅                       8.57                       8.64   
43   2719     燦星旅                      11.94                      13.07   
44   2724   富驛-KY                      -7.62                      14.79   
45   2726   雅茗-KY                      52.92                      54.59   
46   2729    瓦城泰統                      53.73                      53.32   
47   2732    六角國際                      49.21                      54.84   
48   2734     易飛網                      17.62                      12.61   
49   2736      高野                      52.48                      52.51   
50   2740      天蔥                      46.84                      45.52   
51   2916    滿心企業                      46.92                      48.04   
52   2924   東凌-KY             

In [6]:
#Database-style DataFrame joining/merging: join, merge
#Concatenating objects: concat, append

#ignore_index = True 可以忽略合併時舊的 index 欄位，改採用自動產生的 index
df_gross_profit = pd.concat([df_gross_profit_sii,df_gross_profit_otc],axis=0, ignore_index=True)

df_gross_profit

公司代號     公司名稱 GrossProfitMargin(%)_107Q1 GrossProfitMargin(%)_106Q4  \
0     1101       台泥                      23.95                      19.24   
1     1102       亞泥                      20.09                      15.67   
2     1103       嘉泥                      11.63                      13.47   
3     1104     環球水泥                      11.88                      12.21   
4     1108     幸福水泥                       2.47                       3.74   
5     1109     信大水泥                      22.71                      23.36   
6     1110       東泥                       8.35                      -2.52   
7     1201     味全公司                      28.20                      31.29   
8     1203     味王公司                      33.75                      32.61   
9     1210     大成長城                      14.90                      13.48   
10    1213       大飲                      10.74                      10.54   
11    1215     卜蜂企業                      14.78                      16.75   
12    1216       統一                      33.97                      33.20   
13    1217      愛之味                      31.66                      31.46   
14    1218     泰山企業                      16.56                      17.34   
15    1219     福壽實業                       9.32                       8.28   
16    1220       台榮                      11.49                      11.62   
17    1225      福懋油                       8.99                       9.63   
18    1227       佳格                      30.87                      27.95   
19    1229     聯華實業                      16.62                      21.16   
20    1231     聯華食品                      22.76                      20.56   
21    1232      大統益                      10.43                       9.98   
22    1233       天仁                      58.11                      56.91   
23    1234       黑松                      20.48                      25.69   
24    1235       興泰                     -10.29                       6.24   
25    1236     宏亞食品                      28.20                      26.76   
26    1256  鮮活果汁-KY                      31.63                      29.92   
27    1262    綠悅-KY                       7.73                      22.15   
28    1301       台塑                      17.26                      16.19   
29    1303     南亞塑膠                      16.75                      16.32   
30    1304       台聚                      12.58                      12.26   
31    1305       華夏                      23.41                      18.89   
32    1307     三芳化工                      23.21                      29.46   
33    1308       亞聚                       5.87                      10.88   
34    1309     台達化工                       7.75                       7.23   
35    1310       台苯                      13.64                      11.45   
36    1312     國喬石化                      17.61                      16.25   
37    1313       聯成                       7.51                       7.63   
38    1314      中石化                      13.25                      16.11   
39    1315     達新工業                      14.33                      16.71   
40    1316       上曜                      32.49                      29.35   
41    1319       東陽                      23.43                      24.23   
42    1321       大洋                       6.76                       5.64   
43    1323       永裕                      23.66                      23.64   
44    1324     地球工業                      14.99                      15.22   
45    1325       恒大                      11.55                      13.66   
46    1326       台化                      15.92                      14.84   
47    1337    再生-KY                     -12.37                      15.07   
48    1338    廣華-KY                      25.25                      26.41   
49    1339       昭輝                      30.02                      30.96   
50    1340    勝悅-KY                      28.59                      34.39   
51

In [7]:
#檢查column資料型態

#df_gross_profit.info() #non-null object
#df_gross_profit.dtypes #object
#df_gross_profit.applymap(np.isreal) #all False
'''
公司代號              int64
公司名稱             object
GrossProfit(%)_107Q1    float64
GrossProfit(%)_106Q4    float64
GrossProfit(%)_106Q3    float64
GrossProfit(%)_106Q2    float64
GrossProfit(%)_106Q1    float64
GrossProfit(%)_105Q4    float64
GrossProfit(%)_105Q3    float64
GrossProfit(%)_105Q2    float64
GrossProfit(%)_105Q1    float64
GrossProfit(%)_104Q4    float64
GrossProfit(%)_104Q3    float64
GrossProfit(%)_104Q2    float64
GrossProfit(%)_104Q1    float64
dtype: object
'''

df_gross_profit = df_gross_profit.convert_objects(convert_numeric=True) #轉成float型態方便後續處理

df_gross_profit.convert_objects(convert_numeric=True).dtypes #轉成float型態方便後續處理

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:25: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:27: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


公司代號                            int64
公司名稱                           object
GrossProfitMargin(%)_107Q1    float64
GrossProfitMargin(%)_106Q4    float64
GrossProfitMargin(%)_106Q3    float64
GrossProfitMargin(%)_106Q2    float64
GrossProfitMargin(%)_106Q1    float64
GrossProfitMargin(%)_105Q4    float64
GrossProfitMargin(%)_105Q3    float64
GrossProfitMargin(%)_105Q2    float64
GrossProfitMargin(%)_105Q1    float64
GrossProfitMargin(%)_104Q4    float64
GrossProfitMargin(%)_104Q3    float64
GrossProfitMargin(%)_104Q2    float64
GrossProfitMargin(%)_104Q1    float64
dtype: object

In [8]:
def isFloat(element):  
    try:
        float(element)
        return True
    except ValueError:
        return False

In [9]:
def growth_func(row, year, season):
    previous_year = year - 1
    #判斷是否為文字而非數字
    if(isFloat(row['GrossProfitMargin(%)_{0}Q{1}'.format(year, season)]) == True):
        subsequent_value = float(row['GrossProfitMargin(%)_{0}Q{1}'.format(year, season)])
        previous_value = float(row['GrossProfitMargin(%)_{0}Q{1}'.format(previous_year, season)])
   
        if(previous_value == 0):
            result = ((subsequent_value - previous_value)/np.abs(subsequent_value))*100
        else:
            result = ((subsequent_value - previous_value)/np.abs(previous_value))*100            
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
     
    else:
        return 'NoValue'

In [10]:
def ma2q_growth_func(row, year, season):
    #判斷是否為文字而非數字
    if(isFloat(row['GrossProfitMargin(%)_{0}Q{1}'.format(year, season)]) == True):
        previous_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        subsequent_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        
        result = ((subsequent_value + previous_value)/2)
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
    
    else:
        return 'NoValue'

In [11]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = 107
season = 1
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4)):
    df_gross_profit['Growth_{0}Q{1}'.format(year, season)] = df_gross_profit.apply (lambda row: growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [12]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = 107
season = 1
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4-1)):
    df_gross_profit['2QMAGrowth_{0}Q{1}'.format(year, season)] = df_gross_profit.apply (lambda row: ma2q_growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [13]:
# pandas styling
def color_white(val):
    """
    Takes a scalar and returns a string with
    the css property `'color: red'` for negative
    strings, black otherwise.
    """
    color = 'white'
    return 'color: %s' % color

def background_color(val):    
    if float(val) < 0:
        backgroundcolor = '#ff0000'
    elif float(val) < 10:
        backgroundcolor = '#f47721'
    elif float(val) < 20:
        backgroundcolor = '#ffdd00'
    elif float(val) < 30:
        backgroundcolor = '#5ecc62'
    else:
        backgroundcolor = '#00ad45'
    return 'background-color: %s' % backgroundcolor

In [14]:
def get_basic_info_for_ftock(stocktype):

    #get basic info of company
    '''
    抓取上市櫃股票的代號、名稱...等資料。
    上市
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=2
    上櫃
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=4
    '''
    #http://bloggerkaiweng.blogspot.com/2016/09/python.html

    if(stocktype == 'sii'):
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=2'
    else:
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=4'
    
    r = requests.get(url, stream=True, verify=False, proxies=proxyDict)
    r.encoding = 'big5hkscs' 
    dfshow = pd.read_html(r.text)

    for i, df in enumerate(dfshow):
        df.columns = df.iloc[0]
        dfshow[i] = df.iloc[1:]

    df = pd.concat(dfshow).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df['有價證券代號及名稱'] != '股票']
    df = df[~df['有價證券代號及名稱'].isnull()]
    df = df.reset_index(drop=True)
    
    newdf=df[df['產業別'] > '0']
    del newdf['國際證券辨識號碼(ISIN Code)'],newdf['CFICode'],newdf['備註']

    df2=newdf['有價證券代號及名稱'].str.split(' ', expand=True)
    df2 = df2.reset_index(drop=True)
    newdf = newdf.reset_index(drop=True)
    for i in df2.index:
        if '　' in df2.iat[i,0]:
            df2.iat[i,1]=df2.iat[i,0].split('　')[1]
            df2.iat[i,0]=df2.iat[i,0].split('　')[0]
    newdf=df2.join(newdf)
    newdf=newdf.rename(columns = {0:'公司代號',1:'股票名稱'})
    del newdf['有價證券代號及名稱']

    return newdf

In [15]:
df_basicinfo_sii = get_basic_info_for_ftock('sii').convert_objects(convert_numeric=True) #轉成float型態
df_basicinfo_otc = get_basic_info_for_ftock('otc').convert_objects(convert_numeric=True) #轉成float型態

df_basicinfo = pd.concat([df_basicinfo_sii,df_basicinfo_otc],axis=0, ignore_index=True)
#df_eps_basicinfo_sii.dtypes
#df_eps_basicinfo_otc

df_gross_profit = df_gross_profit.merge(df_basicinfo, on='公司代號', how='inner')

df_gross_profit

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  """Entry point for launching an IPython kernel.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  


公司代號     公司名稱  GrossProfitMargin(%)_107Q1  GrossProfitMargin(%)_106Q4  \
0     1101       台泥                       23.95                       19.24   
1     1102       亞泥                       20.09                       15.67   
2     1103       嘉泥                       11.63                       13.47   
3     1104     環球水泥                       11.88                       12.21   
4     1108     幸福水泥                        2.47                        3.74   
5     1109     信大水泥                       22.71                       23.36   
6     1110       東泥                        8.35                       -2.52   
7     1201     味全公司                       28.20                       31.29   
8     1203     味王公司                       33.75                       32.61   
9     1210     大成長城                       14.90                       13.48   
10    1213       大飲                       10.74                       10.54   
11    1215     卜蜂企業                       14.78                       16.75   
12    1216       統一                       33.97                       33.20   
13    1217      愛之味                       31.66                       31.46   
14    1218     泰山企業                       16.56                       17.34   
15    1219     福壽實業                        9.32                        8.28   
16    1220       台榮                       11.49                       11.62   
17    1225      福懋油                        8.99                        9.63   
18    1227       佳格                       30.87                       27.95   
19    1229     聯華實業                       16.62                       21.16   
20    1231     聯華食品                       22.76                       20.56   
21    1232      大統益                       10.43                        9.98   
22    1233       天仁                       58.11                       56.91   
23    1234       黑松                       20.48                       25.69   
24    1235       興泰                      -10.29                        6.24   
25    1236     宏亞食品                       28.20                       26.76   
26    1256  鮮活果汁-KY                       31.63                       29.92   
27    1262    綠悅-KY                        7.73                       22.15   
28    1301       台塑                       17.26                       16.19   
29    1303     南亞塑膠                       16.75                       16.32   
30    1304       台聚                       12.58                       12.26   
31    1305       華夏                       23.41                       18.89   
32    1307     三芳化工                       23.21                       29.46   
33    1308       亞聚                        5.87                       10.88   
34    1309     台達化工                        7.75                        7.23   
35    1310       台苯                       13.64                       11.45   
36    1312     國喬石化                       17.61                       16.25   
37    1313       聯成                        7.51                        7.63   
38    1314      中石化                       13.25                       16.11   
39    1315     達新工業                       14.33                       16.71   
40    1316       上曜                       32.49                       29.35   
41    1319       東陽                       23.43                       24.23   
42    1321       大洋                        6.76                        5.64   
43    1323       永裕                       23.66                       23.64   
44    1324     地球工業                       14.99                       15.22   
45    1325       恒大                       11.55                       13.66   
46    1326       台化                       15.92                       14.84   
47    1337    再生-KY                      -12.37                       15.07   
48    1338    廣華-KY                       25.25                       26.41   
49    1339       昭輝                       30.02         

In [16]:
# styled dataframe can use .to_excel('Styled_Basic_EPS.xlsx', engine='openpyxl') to export excel with style
year = 107
season = 1
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
columns_name = []
for i in range(int(howmany_year_data*4-4)):
    columns_name.append('Growth_{0}Q{1}'.format(year, season))
    columns_name.append('2QMAGrowth_{0}Q{1}'.format(year, season))
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

print(columns_name)
# the cell’s style depends only on it’s own value. That means we should use the Styler.applymap method which works elementwise.
# Now suppose you wanted to highlight the maximum value in each column. We can’t use .applymap anymore since that operated elementwise. Instead, we’ll turn to .apply which operates columnwise (or rowwise using the axis keyword).
#df_eps.style.applymap(color_negative_red, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).applymap(background_color, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).to_excel('Styled_Basic_EPS.xlsx', 'EPS_Basic', engine='openpyxl')
df_gross_profit.style.applymap(color_white, subset=pd.IndexSlice[:, columns_name]).applymap(background_color, subset=pd.IndexSlice[:, columns_name]).to_excel('Styled_Basic_Perspective_GrossProfitMargin.xlsx', 'GrossProfitMargin_Basic', engine='openpyxl')

# Pandas style function to hignlight specific columns
# http://pandas.pydata.org/pandas-docs/stable/style.html#Finer-Control:-Slicing
# Finer Control: Slicing
# ex: df.style.apply(highlight_max, subset=['B', 'C', 'D'])

['Growth_107Q1', '2QMAGrowth_107Q1', 'Growth_106Q4', '2QMAGrowth_106Q4', 'Growth_106Q3', '2QMAGrowth_106Q3', 'Growth_106Q2', '2QMAGrowth_106Q2', 'Growth_106Q1', '2QMAGrowth_106Q1', 'Growth_105Q4', '2QMAGrowth_105Q4', 'Growth_105Q3', '2QMAGrowth_105Q3', 'Growth_105Q2', '2QMAGrowth_105Q2']


C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\pandas\core\indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)
